# Working with Pandas I
#### Based on the Chapter 5 of the book "Python for Data Analysis" by Wes McKinney
Prepared by Dr. Kalpakis for CMSC 491/691, Fall 2017

In [1]:
import pandas as pd
import random
import re

## 1-d Series
a series is a fixed-length dictionary with keys in sorted order

Panda indexes (axes labels) are of these types: Index, Int64Index, MultiIndex, DateTimeInddex, PeriodIndex
Columns and rows are often associated with suhc indexes (labels)

In [2]:
#create 1-d sequence with 4 values and given labels in index
obj = pd.Series([35000, 71000, 16000, 5000], index=['Ohio', 'Texas', 'Oregon', 'Utah'])
print(obj.values)
print(obj.index)
# get subset of given labels
obj[['Ohio', 'Utah']]

[35000 71000 16000  5000]
Index(['Ohio', 'Texas', 'Oregon', 'Utah'], dtype='object')


Ohio    35000
Utah     5000
dtype: int64

In [3]:
#create a series from a dictionary as well
data = {'Ohio': 35000, 'Texas': 71000, 'Oregon': 16000, 'Utah': 5000}
obj = pd.Series(data)
obj

Ohio      35000
Oregon    16000
Texas     71000
Utah       5000
dtype: int64

In [4]:
#if a label doesn't have an associated value in dict then set it to NaN
states = ['California', 'Ohio', 'Oregon', 'Texas']
obj2 = pd.Series(data, index=states)
obj2

California        NaN
Ohio          35000.0
Oregon        16000.0
Texas         71000.0
dtype: float64

In [5]:
#series objects auto-align along their index
obj+obj2

California         NaN
Ohio           70000.0
Oregon         32000.0
Texas         142000.0
Utah               NaN
dtype: float64

In [6]:
#can update Series in place
obj2.index = ['CA', 'OH', 'OR', 'TX']
obj2

CA        NaN
OH    35000.0
OR    16000.0
TX    71000.0
dtype: float64

## DataFrames: 2-d tabular data

In [7]:
# create dataframe from dictionary columns and given row and column labels
# notice the NaN's in the column missing from the dictionary
data = {'state': ['Ohio', 'Ohio', 'Ohio', 'Nevada', 'Nevada'],
    'year': [2000, 2001, 2002, 2001, 2002],
    'pop': [1.5, 1.7, 3.6, 2.4, 2.9]}
rowLabels = ['one', 'two', 'three', 'four', 'five']
columnLabels=['year', 'state', 'pop', 'debt']
frame = pd.DataFrame(data, columns=columnLabels, index=rowLabels)
print(frame.columns) # the column labels (series)
print(frame.index) # the row labels (series)
frame

Index(['year', 'state', 'pop', 'debt'], dtype='object')
Index(['one', 'two', 'three', 'four', 'five'], dtype='object')


year   state  pop debt
one    2000    Ohio  1.5  NaN
two    2001    Ohio  1.7  NaN
three  2002    Ohio  3.6  NaN
four   2001  Nevada  2.4  NaN
five   2002  Nevada  2.9  NaN

In [8]:
#subset by columns
frame[['state', 'year']]

state  year
one      Ohio  2000
two      Ohio  2001
three    Ohio  2002
four   Nevada  2001
five   Nevada  2002

In [9]:
#subset by row labels
frame.loc[['one', 'three']]

year state  pop debt
one    2000  Ohio  1.5  NaN
three  2002  Ohio  3.6  NaN

In [10]:
#subset by both row and column labels
frame.loc[['one', 'three']][['state', 'year']]

state  year
one    Ohio  2000
three  Ohio  2002

In [11]:
# subset by row index and column labels
frame[:2][['state', 'year']]

state  year
one  Ohio  2000
two  Ohio  2001

In [12]:
#subset by value (boolean expression)
frame[ frame['pop'] > 2]

year   state  pop debt
three  2002    Ohio  3.6  NaN
four   2001  Nevada  2.4  NaN
five   2002  Nevada  2.9  NaN

In [13]:
#assign values to a column
frame['debt'] = [random.randint(-10, 0) for _ in range(5)]
frame

year   state  pop  debt
one    2000    Ohio  1.5    -6
two    2001    Ohio  1.7    -5
three  2002    Ohio  3.6   -10
four   2001  Nevada  2.4    -9
five   2002  Nevada  2.9    -2

In [14]:
# assign values to some rows of a column (with NaN for all the others): use a series object
val = pd.Series([-1.2, -1.5, -1.7], index=['two', 'four', 'five'])
frame['debt'] = val
frame

year   state  pop  debt
one    2000    Ohio  1.5   NaN
two    2001    Ohio  1.7  -1.2
three  2002    Ohio  3.6   NaN
four   2001  Nevada  2.4  -1.5
five   2002  Nevada  2.9  -1.7

In [15]:
# create a new column and initialize it with an expression
frame['tmp'] = frame.state == 'Ohio'
frame

year   state  pop  debt    tmp
one    2000    Ohio  1.5   NaN   True
two    2001    Ohio  1.7  -1.2   True
three  2002    Ohio  3.6   NaN   True
four   2001  Nevada  2.4  -1.5  False
five   2002  Nevada  2.9  -1.7  False

In [16]:
#delete a column
del frame['tmp']
frame

year   state  pop  debt
one    2000    Ohio  1.5   NaN
two    2001    Ohio  1.7  -1.2
three  2002    Ohio  3.6   NaN
four   2001  Nevada  2.4  -1.5
five   2002  Nevada  2.9  -1.7

In [17]:
#create dataframe from dict of dicts (outer dict gives the columns, inner dict  the rows)
pop = {'Nevada': {2001: 2.4, 2002: 2.9},
       'Ohio': {2000: 1.5, 2001: 1.7, 2002: 3.6}}
frame2 = pd.DataFrame(pop)
frame2

Nevada  Ohio
2000     NaN   1.5
2001     2.4   1.7
2002     2.9   3.6

In [18]:
#re-index pandas by subsetting existing rows and adding new rows with fill-in value
frame3 = frame.reindex(['one', 'two', 'six'], fill_value=100)
frame3

year state    pop   debt
one  2000  Ohio    1.5    NaN
two  2001  Ohio    1.7   -1.2
six   100   100  100.0  100.0

In [19]:
frame3.drop(['six'])

year state  pop  debt
one  2000  Ohio  1.5   NaN
two  2001  Ohio  1.7  -1.2

### Apply functions to dataframe elements

In [20]:
import numpy as np
# apply element-wise functions
data = frame[['debt', 'pop']]
np.exp(data)

debt        pop
one         NaN   4.481689
two    0.301194   5.473947
three       NaN  36.598234
four   0.223130  11.023176
five   0.182684  18.174145

In [21]:
f = lambda x: x.max() - x.min()
print('by col\n\n', data.apply(f)) # aply f to each column (axis=0)
print('by row\n\n', data.apply(f, axis=1)) # apply f to each row (along axis 1)

by col

 debt    0.5
pop     2.1
dtype: float64
by row

 one      0.0
two      2.9
three    0.0
four     3.9
five     4.6
dtype: float64


In [22]:
# apply a function to each column; return a new frame
def f(x): return pd.Series([x.min(), x.max()], index=['min', 'max'])
ff = data.apply(f)
ff

debt  pop
min  -1.7  1.5
max  -1.2  3.6

### Dataframe sort, rank, and summarize

In [23]:
frame.sort_index(axis=0, ascending=True) # sort by rows


year   state  pop  debt
five   2002  Nevada  2.9  -1.7
four   2001  Nevada  2.4  -1.5
one    2000    Ohio  1.5   NaN
three  2002    Ohio  3.6   NaN
two    2001    Ohio  1.7  -1.2

In [24]:
frame.sort_values(by=['state', 'pop']) # sort by columns

year   state  pop  debt
four   2001  Nevada  2.4  -1.5
five   2002  Nevada  2.9  -1.7
one    2000    Ohio  1.5   NaN
two    2001    Ohio  1.7  -1.2
three  2002    Ohio  3.6   NaN

In [25]:
# get the rank of the values at each column
frame.rank()

year  state  pop  debt
one     1.0    4.0  1.0   NaN
two     2.5    4.0  2.0   3.0
three   4.5    4.0  5.0   NaN
four    2.5    1.5  3.0   2.0
five    4.5    1.5  4.0   1.0

In [26]:
frame

year   state  pop  debt
one    2000    Ohio  1.5   NaN
two    2001    Ohio  1.7  -1.2
three  2002    Ohio  3.6   NaN
four   2001  Nevada  2.4  -1.5
five   2002  Nevada  2.9  -1.7

In [27]:
# aggregate the values of each column
frame.sum()

year                        10006
state    OhioOhioOhioNevadaNevada
pop                          12.1
debt                         -4.4
dtype: object

In [28]:
#get basic statistical description for each column
frame.describe()

year       pop      debt
count     5.00000  5.000000  3.000000
mean   2001.20000  2.420000 -1.466667
std       0.83666  0.864292  0.251661
min    2000.00000  1.500000 -1.700000
25%    2001.00000  1.700000 -1.600000
50%    2001.00000  2.400000 -1.500000
75%    2002.00000  2.900000 -1.350000
max    2002.00000  3.600000 -1.200000

In [29]:
#compute correlation of two series (columns)
frame['pop'].corr(frame['year'])

0.89197029966839891

In [30]:
#compute the pair-wise correlations of a frame's columns
frame.corr()

year       pop      debt
year  1.000000  0.891970 -0.802955
pop   0.891970  1.000000 -0.999819
debt -0.802955 -0.999819  1.000000

In [31]:
# drop rows with NaN
frame.dropna()
# drop columns with NaN using axis=1

year   state  pop  debt
two   2001    Ohio  1.7  -1.2
four  2001  Nevada  2.4  -1.5
five  2002  Nevada  2.9  -1.7

In [32]:
#fill missing values
frame.fillna(-99999)

year   state  pop     debt
one    2000    Ohio  1.5 -99999.0
two    2001    Ohio  1.7     -1.2
three  2002    Ohio  3.6 -99999.0
four   2001  Nevada  2.4     -1.5
five   2002  Nevada  2.9     -1.7

## Hierarchical indexes

In [33]:
#index labels are now tuples - re
data = pd.Series( [random.random() for _ in range(10)], 
              index=[['a', 'a', 'a', 'b', 'b', 'b', 'c', 'c', 'd', 'd'], 
                     [1, 2, 3, 1, 2, 3, 1, 2, 2, 3]])
data

a  1    0.877418
   2    0.245937
   3    0.923737
b  1    0.370765
   2    0.299855
   3    0.257263
c  1    0.173912
   2    0.570717
d  2    0.473231
   3    0.030142
dtype: float64

In [34]:
data.index

MultiIndex(levels=[['a', 'b', 'c', 'd'], [1, 2, 3]],
           labels=[[0, 0, 0, 1, 1, 1, 2, 2, 3, 3], [0, 1, 2, 0, 1, 2, 0, 1, 1, 2]])

In [35]:
#subsetting by outermost index
data['b':'c']

b  1    0.370765
   2    0.299855
   3    0.257263
c  1    0.173912
   2    0.570717
dtype: float64

In [36]:
# for 2-tuples for index of series can be converted to a table with unstack()
data.unstack()

1         2         3
a  0.877418  0.245937  0.923737
b  0.370765  0.299855  0.257263
c  0.173912  0.570717       NaN
d       NaN  0.473231  0.030142

In [37]:
# hierarchical indexes can be used for tabular pandas as well
frame = pd.DataFrame(np.arange(12).reshape((4, 3)),
    index=[['a', 'a', 'b', 'b'], [1, 2, 1, 2]],
    columns=[['Ohio', 'Ohio', 'Colorado'],
     ['Green', 'Red', 'Green']])
# name the components of the hierarchical row and column indexes
frame.index.names = ['key1', 'key2']
frame.columns.names = ['state', 'color']
frame

state      Ohio     Colorado
color     Green Red    Green
key1 key2                   
a    1        0   1        2
     2        3   4        5
b    1        6   7        8
     2        9  10       11

In [38]:
# aggregate by sub-index
frame.sum(level='key2')

state  Ohio     Colorado
color Green Red    Green
key2                    
1         6   8       10
2        12  14       16

In [39]:
frame.sum(level='color', axis=1)

color      Green  Red
key1 key2            
a    1         2    1
     2         8    4
b    1        14    7
     2        20   10

## Combine pandas: merge and concat

In [40]:
df1 = pd.DataFrame({'key': ['b', 'b', 'a', 'c', 'a', 'a', 'b'], 'data1': range(7)})
df2 = pd.DataFrame({'key': ['a', 'b', 'd'], 'data2': range(3)})

In [41]:
df1

data1 key
0      0   b
1      1   b
2      2   a
3      3   c
4      4   a
5      5   a
6      6   b

In [42]:
df2

data2 key
0      0   a
1      1   b
2      2   d

In [43]:
pd.merge(df1, df2) # merge on index

data1 key  data2
0      0   b      1
1      1   b      1
2      6   b      1
3      2   a      0
4      4   a      0
5      5   a      0

In [44]:
pd.merge(df1, df2, on='key') #merge on another column
# argumnents how=One of 'inner', 'outer', 'left' or 'right'. 'inner' by default
#  suffix= suffix to append to column names in case of overlaps

data1 key  data2
0      0   b      1
1      1   b      1
2      6   b      1
3      2   a      0
4      4   a      0
5      5   a      0

In [45]:
# concat pandas along an axis
pd.concat([df1, df2], axis=1)

data1 key  data2  key
0      0   b    0.0    a
1      1   b    1.0    b
2      2   a    2.0    d
3      3   c    NaN  NaN
4      4   a    NaN  NaN
5      5   a    NaN  NaN
6      6   b    NaN  NaN